In [1]:
import argparse
import datetime
import os
import re
os.environ.setdefault("TF_CPP_MIN_LOG_LEVEL", "2") # Report only TF errors by default

import numpy as np
import tensorflow as tf

from uppercase_data import UppercaseData

In [14]:
# TODO: Set reasonable values for the hyperparameters, notably
# for `alphabet_size` and `window` and others.
parser = argparse.ArgumentParser()
parser.add_argument("--alphabet_size", default=100, type=int, help="If nonzero, limit alphabet to this many most frequent chars.")
parser.add_argument("--batch_size", default=64, type=int, help="Batch size.")
parser.add_argument("--epochs", default=1, type=int, help="Number of epochs.")
parser.add_argument("--seed", default=42, type=int, help="Random seed.")
parser.add_argument("--threads", default=1, type=int, help="Maximum number of threads to use.")
parser.add_argument("--window", default=3, type=int, help="Window size to use.")
# additional
parser.add_argument("--dropout", default=0.5, type=float, help="Dropout rate.")

args = parser.parse_args([] if "__file__" not in globals() else None)
print(args)

# Fix random seeds and threads
tf.keras.utils.set_random_seed(args.seed)
tf.config.threading.set_inter_op_parallelism_threads(args.threads)
tf.config.threading.set_intra_op_parallelism_threads(args.threads)

    
# Create logdir name
args.logdir = os.path.join("logs", "{}-{}-{}".format(
    os.path.basename(globals().get("__file__", "notebook")),
    datetime.datetime.now().strftime("%Y-%m-%d_%H%M%S"),
    ",".join(("{}={}".format(re.sub("(.)[^_]*_?", r"\1", key), value) for key, value in sorted(vars(args).items())))
))

Namespace(alphabet_size=100, batch_size=64, epochs=1, seed=42, threads=1, window=3, dropout=0.5)


In [10]:
# Load data
uppercase_data = UppercaseData(args.window, args.alphabet_size)

In [8]:
train_data = uppercase_data.train.data
for i, (window, label) in enumerate(zip(train_data['windows'], train_data['labels'])):
    print(i, window, [uppercase_data.train.alphabet[i] for i in window], label)

0 [ 0  0  0 12  2  3 24] ['<pad>', '<pad>', '<pad>', 'v', ' ', 'o', 'b'] 1
1 [ 0  0 12  2  3 24 14] ['<pad>', '<pad>', 'v', ' ', 'o', 'b', 'd'] 0
2 [ 0 12  2  3 24 14  3] ['<pad>', 'v', ' ', 'o', 'b', 'd', 'o'] 0
3 [12  2  3 24 14  3 24] ['v', ' ', 'o', 'b', 'd', 'o', 'b'] 0
4 [ 2  3 24 14  3 24 19] [' ', 'o', 'b', 'd', 'o', 'b', 'í'] 0
5 [ 3 24 14  3 24 19  2] ['o', 'b', 'd', 'o', 'b', 'í', ' '] 0
6 [24 14  3 24 19  2 17] ['b', 'd', 'o', 'b', 'í', ' ', 'p'] 0
7 [14  3 24 19  2 17 11] ['d', 'o', 'b', 'í', ' ', 'p', 'r'] 0
8 [ 3 24 19  2 17 11  3] ['o', 'b', 'í', ' ', 'p', 'r', 'o'] 0
9 [24 19  2 17 11  3 20] ['b', 'í', ' ', 'p', 'r', 'o', 'h'] 0
10 [19  2 17 11  3 20  9] ['í', ' ', 'p', 'r', 'o', 'h', 'i'] 0
11 [ 2 17 11  3 20  9 24] [' ', 'p', 'r', 'o', 'h', 'i', 'b'] 0
12 [17 11  3 20  9 24  9] ['p', 'r', 'o', 'h', 'i', 'b', 'i'] 0
13 [11  3 20  9 24  9 18] ['r', 'o', 'h', 'i', 'b', 'i', 'c'] 0
14 [ 3 20  9 24  9 18  4] ['o', 'h', 'i', 'b', 'i', 'c', 'e'] 0
15 [20  9 24  9 18  4  2] 

609 [ 2  6  4 24  3  2  8] [' ', 'n', 'e', 'b', 'o', ' ', 't'] 0
610 [ 6  4 24  3  2  8 28] ['n', 'e', 'b', 'o', ' ', 't', 'é'] 0
611 [ 4 24  3  2  8 28 34] ['e', 'b', 'o', ' ', 't', 'é', 'ž'] 0
612 [24  3  2  8 28 34  2] ['b', 'o', ' ', 't', 'é', 'ž', ' '] 0
613 [ 3  2  8 28 34  2  4] ['o', ' ', 't', 'é', 'ž', ' ', 'e'] 0
614 [ 2  8 28 34  2  4 21] [' ', 't', 'é', 'ž', ' ', 'e', 'z'] 0
615 [ 8 28 34  2  4 21 20] ['t', 'é', 'ž', ' ', 'e', 'z', 'h'] 0
616 [28 34  2  4 21 20  3] ['é', 'ž', ' ', 'e', 'z', 'h', 'o'] 1
617 [34  2  4 21 20  3 12] ['ž', ' ', 'e', 'z', 'h', 'o', 'v'] 0
618 [ 2  4 21 20  3 12  8] [' ', 'e', 'z', 'h', 'o', 'v', 't'] 0
619 [ 4 21 20  3 12  8  4] ['e', 'z', 'h', 'o', 'v', 't', 'e'] 0
620 [21 20  3 12  8  4 23] ['z', 'h', 'o', 'v', 't', 'e', 'j'] 0
621 [20  3 12  8  4 23 43] ['h', 'o', 'v', 't', 'e', 'j', ')'] 0
622 [ 3 12  8  4 23 43 29] ['o', 'v', 't', 'e', 'j', ')', ','] 0
623 [12  8  4 23 43 29  2] ['v', 't', 'e', 'j', ')', ',', ' '] 0
624 [ 8  4 23 43 29  2 18

1234 [11  5  2 12  4  2 12] ['r', 'a', ' ', 'v', 'e', ' ', 'v'] 0
1235 [ 5  2 12  4  2 12  4] ['a', ' ', 'v', 'e', ' ', 'v', 'e'] 0
1236 [ 2 12  4  2 12  4  6] [' ', 'v', 'e', ' ', 'v', 'e', 'n'] 0
1237 [12  4  2 12  4  6 16] ['v', 'e', ' ', 'v', 'e', 'n', 'u'] 1
1238 [ 4  2 12  4  6 16  7] ['e', ' ', 'v', 'e', 'n', 'u', 's'] 0
1239 [ 2 12  4  6 16  7  9] [' ', 'v', 'e', 'n', 'u', 's', 'i'] 0
1240 [12  4  6 16  7  9 16] ['v', 'e', 'n', 'u', 's', 'i', 'u'] 0
1241 [ 4  6 16  7  9 16 26] ['e', 'n', 'u', 's', 'i', 'u', '.'] 0
1242 [ 6 16  7  9 16 26 30] ['n', 'u', 's', 'i', 'u', '.', '\n'] 0
1243 [16  7  9 16 26 30 20] ['u', 's', 'i', 'u', '.', '\n', 'h'] 0
1244 [ 7  9 16 26 30 20 11] ['s', 'i', 'u', '.', '\n', 'h', 'r'] 0
1245 [ 9 16 26 30 20 11 14] ['i', 'u', '.', '\n', 'h', 'r', 'd'] 0
1246 [16 26 30 20 11 14 10] ['u', '.', '\n', 'h', 'r', 'd', 'l'] 1
1247 [26 30 20 11 14 10  3] ['.', '\n', 'h', 'r', 'd', 'l', 'o'] 0
1248 [30 20 11 14 10  3 31] ['\n', 'h', 'r', 'd', 'l', 'o', 'ř'] 0
124

1859 [ 2  8  5  2 12  4  2] [' ', 't', 'a', ' ', 'v', 'e', ' '] 0
1860 [ 8  5  2 12  4  2  7] ['t', 'a', ' ', 'v', 'e', ' ', 's'] 0
1861 [ 5  2 12  4  2  7 17] ['a', ' ', 'v', 'e', ' ', 's', 'p'] 0
1862 [ 2 12  4  2  7 17  3] [' ', 'v', 'e', ' ', 's', 'p', 'o'] 0
1863 [12  4  2  7 17  3 23] ['v', 'e', ' ', 's', 'p', 'o', 'j'] 0
1864 [ 4  2  7 17  3 23  4] ['e', ' ', 's', 'p', 'o', 'j', 'e'] 0
1865 [ 2  7 17  3 23  4  6] [' ', 's', 'p', 'o', 'j', 'e', 'n'] 0
1866 [ 7 17  3 23  4  6 19] ['s', 'p', 'o', 'j', 'e', 'n', 'í'] 0
1867 [17  3 23  4  6 19  2] ['p', 'o', 'j', 'e', 'n', 'í', ' '] 0
1868 [ 3 23  4  6 19  2 15] ['o', 'j', 'e', 'n', 'í', ' ', 'm'] 0
1869 [23  4  6 19  2 15 25] ['j', 'e', 'n', 'í', ' ', 'm', 'y'] 0
1870 [ 4  6 19  2 15 25  7] ['e', 'n', 'í', ' ', 'm', 'y', 's'] 0
1871 [ 6 19  2 15 25  7 10] ['n', 'í', ' ', 'm', 'y', 's', 'l'] 0
1872 [19  2 15 25  7 10  9] ['í', ' ', 'm', 'y', 's', 'l', 'i'] 0
1873 [ 2 15 25  7 10  9  2] [' ', 'm', 'y', 's', 'l', 'i', ' '] 0
1874 [15 2

2484 [19 18 20  2 13 11  5] ['í', 'c', 'h', ' ', 'k', 'r', 'a'] 0
2485 [18 20  2 13 11  5 10] ['c', 'h', ' ', 'k', 'r', 'a', 'l'] 1
2486 [20  2 13 11  5 10  3] ['h', ' ', 'k', 'r', 'a', 'l', 'o'] 0
2487 [ 2 13 11  5 10  3 12] [' ', 'k', 'r', 'a', 'l', 'o', 'v'] 0
2488 [13 11  5 10  3 12  9] ['k', 'r', 'a', 'l', 'o', 'v', 'i'] 0
2489 [11  5 10  3 12  9 18] ['r', 'a', 'l', 'o', 'v', 'i', 'c'] 0
2490 [ 5 10  3 12  9 18  2] ['a', 'l', 'o', 'v', 'i', 'c', ' '] 0
2491 [10  3 12  9 18  2  5] ['l', 'o', 'v', 'i', 'c', ' ', 'a'] 0
2492 [ 3 12  9 18  2  5  2] ['o', 'v', 'i', 'c', ' ', 'a', ' '] 0
2493 [12  9 18  2  5  2  6] ['v', 'i', 'c', ' ', 'a', ' ', 'n'] 0
2494 [ 9 18  2  5  2  6  5] ['i', 'c', ' ', 'a', ' ', 'n', 'a'] 0
2495 [18  2  5  2  6  5  2] ['c', ' ', 'a', ' ', 'n', 'a', ' '] 0
2496 [ 2  5  2  6  5  2 24] [' ', 'a', ' ', 'n', 'a', ' ', 'b'] 0
2497 [ 5  2  6  5  2 24 10] ['a', ' ', 'n', 'a', ' ', 'b', 'l'] 0
2498 [ 2  6  5  2 24 10  5] [' ', 'n', 'a', ' ', 'b', 'l', 'a'] 0
2499 [ 6  

...

52328 [18 20 13  3  2 35 16] ['c', 'h', 'k', 'o', ' ', 'š', 'u'] 1
52329 [20 13  3  2 35 16 15] ['h', 'k', 'o', ' ', 'š', 'u', 'm'] 0
52330 [13  3  2 35 16 15  5] ['k', 'o', ' ', 'š', 'u', 'm', 'a'] 1
52331 [ 3  2 35 16 15  5 12] ['o', ' ', 'š', 'u', 'm', 'a', 'v'] 0
52332 [ 2 35 16 15  5 12  5] [' ', 'š', 'u', 'm', 'a', 'v', 'a'] 0
52333 [35 16 15  5 12  5 29] ['š', 'u', 'm', 'a', 'v', 'a', ','] 0
52334 [16 15  5 12  5 29  2] ['u', 'm', 'a', 'v', 'a', ',', ' '] 0
52335 [15  5 12  5 29  2  5] ['m', 'a', 'v', 'a', ',', ' ', 'a'] 0
52336 [ 5 12  5 29  2  5 10] ['a', 'v', 'a', ',', ' ', 'a', 'l'] 0
52337 [12  5 29  2  5 10  4] ['v', 'a', ',', ' ', 'a', 'l', 'e'] 0
52338 [ 5 29  2  5 10  4  2] ['a', ',', ' ', 'a', 'l', 'e', ' '] 0
52339 [29  2  5 10  4  2 17] [',', ' ', 'a', 'l', 'e', ' ', 'p'] 0
52340 [ 2  5 10  4  2 17 10] [' ', 'a', 'l', 'e', ' ', 'p', 'l'] 0
52341 [ 5 10  4  2 17 10  5] ['a', 'l', 'e', ' ', 'p', 'l', 'a'] 0
52342 [10  4  2 17 10  5 12] ['l', 'e', ' ', 'p', 'l', 'a', 'v

52973 [ 7  8  5 11 28 15  2] ['s', 't', 'a', 'r', 'é', 'm', ' '] 0
52974 [ 8  5 11 28 15  2 24] ['t', 'a', 'r', 'é', 'm', ' ', 'b'] 0
52975 [ 5 11 28 15  2 24 11] ['a', 'r', 'é', 'm', ' ', 'b', 'r'] 0
52976 [11 28 15  2 24 11  6] ['r', 'é', 'm', ' ', 'b', 'r', 'n'] 0
52977 [28 15  2 24 11  6 27] ['é', 'm', ' ', 'b', 'r', 'n', 'ě'] 1
52978 [15  2 24 11  6 27 26] ['m', ' ', 'b', 'r', 'n', 'ě', '.'] 0
52979 [ 2 24 11  6 27 26 30] [' ', 'b', 'r', 'n', 'ě', '.', '\n'] 0
52980 [24 11  6 27 26 30 12] ['b', 'r', 'n', 'ě', '.', '\n', 'v'] 0
52981 [11  6 27 26 30 12  5] ['r', 'n', 'ě', '.', '\n', 'v', 'a'] 0
52982 [ 6 27 26 30 12  5 35] ['n', 'ě', '.', '\n', 'v', 'a', 'š'] 0
52983 [27 26 30 12  5 35  4] ['ě', '.', '\n', 'v', 'a', 'š', 'e'] 1
52984 [26 30 12  5 35  4  2] ['.', '\n', 'v', 'a', 'š', 'e', ' '] 0
52985 [30 12  5 35  4  2 23] ['\n', 'v', 'a', 'š', 'e', ' ', 'j'] 0
52986 [12  5 35  4  2 23 15] ['v', 'a', 'š', 'e', ' ', 'j', 'm'] 0
52987 [ 5 35  4  2 23 15 28] ['a', 'š', 'e', ' ', 'j', 

53598 [14  3 16 18 19  2 13] ['d', 'o', 'u', 'c', 'í', ' ', 'k'] 0
53599 [ 3 16 18 19  2 13 10] ['o', 'u', 'c', 'í', ' ', 'k', 'l'] 0
53600 [16 18 19  2 13 10 22] ['u', 'c', 'í', ' ', 'k', 'l', 'á'] 0
53601 [18 19  2 13 10 22 35] ['c', 'í', ' ', 'k', 'l', 'á', 'š'] 0
53602 [19  2 13 10 22 35  8] ['í', ' ', 'k', 'l', 'á', 'š', 't'] 0
53603 [ 2 13 10 22 35  8  4] [' ', 'k', 'l', 'á', 'š', 't', 'e'] 0
53604 [13 10 22 35  8  4 11] ['k', 'l', 'á', 'š', 't', 'e', 'r'] 0
53605 [10 22 35  8  4 11  5] ['l', 'á', 'š', 't', 'e', 'r', 'a'] 0
53606 [22 35  8  4 11  5  2] ['á', 'š', 't', 'e', 'r', 'a', ' '] 0
53607 [35  8  4 11  5  2  5] ['š', 't', 'e', 'r', 'a', ' ', 'a'] 0
53608 [ 8  4 11  5  2  5  2] ['t', 'e', 'r', 'a', ' ', 'a', ' '] 0
53609 [ 4 11  5  2  5  2 21] ['e', 'r', 'a', ' ', 'a', ' ', 'z'] 0
53610 [11  5  2  5  2 21 22] ['r', 'a', ' ', 'a', ' ', 'z', 'á'] 0
53611 [ 5  2  5  2 21 22 11] ['a', ' ', 'a', ' ', 'z', 'á', 'r'] 0
53612 [ 2  5  2 21 22 11  3] [' ', 'a', ' ', 'z', 'á', 'r', 'o

54223 [ 8  2 17 31 19 10  4] ['t', ' ', 'p', 'ř', 'í', 'l', 'e'] 0
54224 [ 2 17 31 19 10  4 34] [' ', 'p', 'ř', 'í', 'l', 'e', 'ž'] 0
54225 [17 31 19 10  4 34  9] ['p', 'ř', 'í', 'l', 'e', 'ž', 'i'] 0
54226 [31 19 10  4 34  9  8] ['ř', 'í', 'l', 'e', 'ž', 'i', 't'] 0
54227 [19 10  4 34  9  8  3] ['í', 'l', 'e', 'ž', 'i', 't', 'o'] 0
54228 [10  4 34  9  8  3  7] ['l', 'e', 'ž', 'i', 't', 'o', 's'] 0
54229 [ 4 34  9  8  3  7  8] ['e', 'ž', 'i', 't', 'o', 's', 't'] 0
54230 [34  9  8  3  7  8  6] ['ž', 'i', 't', 'o', 's', 't', 'n'] 0
54231 [ 9  8  3  7  8  6 27] ['i', 't', 'o', 's', 't', 'n', 'ě'] 0
54232 [ 8  3  7  8  6 27  2] ['t', 'o', 's', 't', 'n', 'ě', ' '] 0
54233 [ 3  7  8  6 27  2  7] ['o', 's', 't', 'n', 'ě', ' ', 's'] 0
54234 [ 7  8  6 27  2  7 17] ['s', 't', 'n', 'ě', ' ', 's', 'p'] 0
54235 [ 8  6 27  2  7 17  3] ['t', 'n', 'ě', ' ', 's', 'p', 'o'] 0
54236 [ 6 27  2  7 17  3 10] ['n', 'ě', ' ', 's', 'p', 'o', 'l'] 0
54237 [27  2  7 17  3 10 16] ['ě', ' ', 's', 'p', 'o', 'l', 'u

KeyboardInterrupt: 

In [27]:
# TODO: Implement a suitable model, optionally including regularization, select
# good hyperparameters and train the model.
#
# The inputs are _windows_ of fixed size (`args.window` characters on left,
# the character in question, and `args.window` characters on right), where
# each character is represented by a `tf.int32` index. To suitably represent
# the characters, you can:
# - Convert the character indices into _one-hot encoding_. There is no
#   explicit Keras layer, but you can
#   - use a Lambda layer which can encompass any function:
#       tf.keras.Sequential([
#         tf.keras.layers.Input(shape=[2 * args.window + 1], dtype=tf.int32),
#         tf.keras.layers.Lambda(lambda x: tf.one_hot(x, len(uppercase_data.train.alphabet))),
#   - or use Functional API and then any TF function can be used
#     as a Keras layer:
#       inputs = tf.keras.layers.Input(shape=[2 * args.window + 1], dtype=tf.int32)
#       encoded = tf.one_hot(inputs, len(uppercase_data.train.alphabet))
#   You can then flatten the one-hot encoded windows and follow with a dense layer.
# - Alternatively, you can use `tf.keras.layers.Embedding` (which is an efficient
#   implementation of one-hot encoding followed by a Dense layer) and flatten afterwards.
model = tf.keras.Sequential()
model.add(tf.keras.layers.Input(shape=[2 * args.window + 1], dtype=tf.int32))
model.add(tf.keras.layers.Lambda(lambda x: tf.one_hot(x, len(uppercase_data.train.alphabet))))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dropout(rate=args.dropout))
model.add(tf.keras.layers.Dense(64, activation=tf.nn.relu))
model.add(tf.keras.layers.Dropout(rate=args.dropout))
model.add(tf.keras.layers.Dense(2 * args.window + 1, activation=tf.nn.softmax))
          

model.compile(
    optimizer=tf.optimizers.Adam()
    #loss=tf.losses.CategoricalCrossentropy(label_smoothing=args.label_smoothing),
    #metrics=[tf.metrics.CategoricalAccuracy(name="accuracy")],
)

model.summary()

Model: "sequential_7"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lambda_5 (Lambda)           (None, 7, 100)            0         
                                                                 
 flatten_3 (Flatten)         (None, 700)               0         
                                                                 
 dropout_2 (Dropout)         (None, 700)               0         
                                                                 
 dense_1 (Dense)             (None, 64)                44864     
                                                                 
 dropout_3 (Dropout)         (None, 64)                0         
                                                                 
 dense_2 (Dense)             (None, 7)                 455       
                                                                 
Total params: 45,319
Trainable params: 45,319
Non-trai

In [ ]:
# TODO: Generate correctly capitalized test set.
# Use `uppercase_data.test.text` as input, capitalize suitable characters,
# and write the result to predictions_file (which is
# `uppercase_test.txt` in the `args.logdir` directory).
os.makedirs(args.logdir, exist_ok=True)
with open(os.path.join(args.logdir, "uppercase_test.txt"), "w", encoding="utf-8") as predictions_file:
    ...